In [1]:
# Copyright 2024 Keysight Technologies Inc.

In [2]:
import numpy as np
import trueq as tq
from trueq.config import GateFactory

basic_config = tq.Config.basic(
    entangler=tq.Gate.cz, connectivity=[(0, 1), (1, 2), (2, 0)]
)
print(basic_config)

Mode: ZXZXZ
Dimension: 2
Gates:
- z(phi):
    Hamiltonian:
    - [Z, phi]
- sx:
    Hamiltonian:
    - [X, 90.0]
- cz:
    Matrix:
    - [1.0, 0.0, 0.0, 0.0]
    - [0.0, 1.0, 0.0, 0.0]
    - [0.0, 0.0, 1.0, 0.0]
    - [0.0, 0.0, 0.0, -1.0]
    Involving: {'(0, 1)': (), '(1, 2)': (), '(2, 0)': ()}



In [3]:
# define iSwap-like gates through a parameterized matrix form
iSwapLike_mat = [
    [1, 0, 0, 0],
    [0, 0, -1j, 0],
    [0, -1j, 0, 0],
    [0, 0, 0, "exp(-1j * phi * pi / 180)"],
]
iSwapLike_factory = GateFactory.from_matrix(name="iSwapLike", matrix=iSwapLike_mat)

In [4]:
parametrized_config = tq.Config.from_parameterized(
    iSwapLike_factory, parameters={(0, 1): 90, (1, 2): 45}
)
print(parametrized_config)

Mode: ZXZ
Dimension: 2
Gates:
- X(phi):
    Hamiltonian:
    - [X, phi]
- Z(phi):
    Hamiltonian:
    - [Z, phi]
- iSwapLike_0_1:
    Matrix:
    - [(0.923879532511+0.382683432365j), 0j, 0j, 0j]
    - [0j, 0j, (0.382683432365-0.923879532511j), 0j]
    - [0j, (0.382683432365-0.923879532511j), 0j, 0j]
    - [0j, 0j, 0j, (0.382683432365-0.923879532511j)]
    Involving: {'(0, 1)': ()}
- iSwapLike_1_2:
    Matrix:
    - [(0.980785280403+0.195090322016j), 0j, 0j, 0j]
    - [0j, 0j, (0.195090322016-0.980785280403j), 0j]
    - [0j, (0.195090322016-0.980785280403j), 0j, 0j]
    - [0j, 0j, 0j, (0.831469612303-0.55557023302j)]
    Involving: {'(1, 2)': ()}



In [5]:
# define a single-qubit gates' parameterization through a Hamiltonian form
u3_factory = GateFactory.from_hamiltonian(
    "U3Gate",
    [["Z", "phi "], ["Y", "theta"], ["Z", "lam"]],
    parameters=["theta", "phi", "lam"],
)

# define a XX(90) entangling gate on the pair (0,1)
xx_factory = GateFactory.from_hamiltonian(
    "XXGate", [["XX", 90]], involving={(0, 1): ()}
)

# construct a configuration from the gate factories
advanced_config = tq.Config([xx_factory, u3_factory])
print(advanced_config)

Mode: ZXZXZ
Dimension: 2
Gates:
- XXGate:
    Hamiltonian:
    - [XX, 90.0]
    Involving: {'(0, 1)': ()}
- U3Gate(theta, phi, lam):
    Hamiltonian:
    - [Z, phi]
    - [Y, theta]
    - [Z, lam]



In [6]:
config = tq.Config.from_yaml("config.yaml")

# Construct the MS gate from this config file:
config.MS(phi=np.pi / 2)

MS(phi)

In [7]:
transpiler = tq.Compiler.from_config(basic_config)

In [8]:
y_circuit = tq.Circuit({0: tq.Gate.y})
y_circuit.draw()

DisplayWrapper(<svg xmlns="http://w...)

In [9]:
# transpile y_circuit, then draw the transpiled result
transpiled_y_circuit = transpiler.compile(y_circuit)
transpiled_y_circuit.draw()

DisplayWrapper(<svg xmlns="http://w...)

In [10]:
# define another example circuit
cx_circuit = tq.Circuit({(0, 1): tq.Gate.cx})
cx_circuit.draw()

# transpile cx_circuit, then draw the transpiled result
transpiled_cx_circuit = transpiler.compile(cx_circuit)
transpiled_cx_circuit.draw()

DisplayWrapper(<svg xmlns="http://w...)